In [198]:
import zipfile
import os

import numpy as np
import seaborn as sns
import pandas as pd
import matplotlib.pyplot as plt

from sklearn import preprocessing
from IPython.display import Image
from matplotlib.patches import Ellipse, PathPatch, Arc, Polygon, Wedge

plt.rcParams['figure.dpi'] = 300

In [199]:
df = pd.read_csv('bldg-MC2.csv')
df.info()
df.describe()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4032 entries, 0 to 4031
Columns: 416 entries, Date/Time to  F_3_Z_11C SUPPLY INLET Mass Flow Rate
dtypes: float64(415), object(1)
memory usage: 12.8+ MB


Drybulb Temperature   Water Heater Tank Temperature  \
count           4032.000000                     4032.000000   
mean              25.206895                       59.124763   
std                2.064292                        0.582666   
min               21.100000                       58.025300   
25%               23.633300                       58.647900   
50%               24.733300                       59.101850   
75%               27.000000                       59.592975   
max               29.400000                       60.747300   

        Water Heater Gas Rate   Supply Side Inlet Mass Flow Rate  \
count             4032.000000                       4.032000e+03   
mean              7725.178544                       3.179000e-01   
std              22591.087212                       5.551804e-17   
min                  0.000000                       3.179000e-01   
25%                  0.000000                       3.179000e-01   
50%                  0.000000                       3.179000e-01   
75%                  0.000000                       3.179000e-01   
max              89340.640800                       3.179000e-01   

        Supply Side Inlet Temperature   Supply Side Outlet Temperature  \
count                     4032.000000                      4032.000000   
mean                        54.318156                        59.124763   
std                          5.350256                         0.582666   
min                         42.115000                        58.025300   
25%                         49.235400                        58.647900   
50%                         56.475900                        59.101850   
75%                         58.888000                        59.592975   
max                         60.792700                        60.747300   

        HVAC Electric Demand Power   Total Electric Demand Power  \
count                  4032.000000                   4032.000000   
mean                  52555.520503                 142274.890509   
std                   32495.398847                  41000.395221   
min                    9301.062100                  73811.181200   
25%                   25316.601250                 110688.755725   
50%                   48191.688300                 138985.708850   
75%                   57611.030025                 181530.125275   
max                  242075.665000                 341392.985000   

        Loop Temp Schedule   Water Heater Setpoint  ...  \
count               4032.0                  4032.0  ...   
mean                  60.0                    60.0  ...   
std                    0.0                     0.0  ...   
min                   60.0                    60.0  ...   
25%                   60.0                    60.0  ...   
50%                   60.0                    60.0  ...   
75%                   60.0                    60.0  ...   
max                   60.0                    60.0  ...   

        F_3_Z_10 SUPPLY INLET Mass Flow Rate  \
count                            4032.000000   
mean                                0.104051   
std                                 0.046793   
min                                 0.027800   
25%                                 0.052175   
50%                                 0.139100   
75%                                 0.139100   
max                                 0.139100   

        F_3_Z_11A RETURN OUTLET CO2 Concentration  \
count                                 4032.000000   
mean                                   579.061553   
std                                    209.961457   
min                                    401.509900   
25%                                    417.273000   
50%                                    499.316100   
75%                                    652.913425   
max                                   1294.654000   

        F_3_Z_11A SUPPLY INLET Temperature  \
count                          4032.000000   
mean        

In [200]:
df.columns

Index(['Date/Time', ' Drybulb Temperature', ' Water Heater Tank Temperature',
       ' Water Heater Gas Rate', ' Supply Side Inlet Mass Flow Rate',
       ' Supply Side Inlet Temperature', ' Supply Side Outlet Temperature',
       ' HVAC Electric Demand Power', ' Total Electric Demand Power',
       ' Loop Temp Schedule',
       ...
       ' F_3_Z_10 SUPPLY INLET Mass Flow Rate',
       ' F_3_Z_11A RETURN OUTLET CO2 Concentration',
       ' F_3_Z_11A SUPPLY INLET Temperature',
       ' F_3_Z_11A SUPPLY INLET Mass Flow Rate',
       ' F_3_Z_11B RETURN OUTLET CO2 Concentration',
       ' F_3_Z_11B SUPPLY INLET Temperature',
       ' F_3_Z_11B SUPPLY INLET Mass Flow Rate',
       ' F_3_Z_11C RETURN OUTLET CO2 Concentration',
       ' F_3_Z_11C SUPPLY INLET Temperature',
       ' F_3_Z_11C SUPPLY INLET Mass Flow Rate'],
      dtype='object', length=416)

In [201]:
features=[' F_2_Z_2 REHEAT COIL Power',' F_2_Z_2 RETURN OUTLET CO2 Concentration',' F_2_Z_2 SUPPLY INLET Mass Flow Rate',
       ' F_2_Z_2 SUPPLY INLET Temperature',' F_2_Z_2 VAV REHEAT Damper Position',' F_2_Z_2: Equipment Power',
       ' F_2_Z_2: Lights Power', ' F_2_Z_2: Thermostat Temp',
       ' F_2_Z_2: Thermostat Cooling Setpoint',' F_2_Z_2: Thermostat Heating Setpoint']
my_df=df[features]
my_df.info()
my_df.describe()
my_df.head()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4032 entries, 0 to 4031
Data columns (total 10 columns):
 #   Column                                    Non-Null Count  Dtype  
---  ------                                    --------------  -----  
 0    F_2_Z_2 REHEAT COIL Power                4032 non-null   float64
 1    F_2_Z_2 RETURN OUTLET CO2 Concentration  4032 non-null   float64
 2    F_2_Z_2 SUPPLY INLET Mass Flow Rate      4032 non-null   float64
 3    F_2_Z_2 SUPPLY INLET Temperature         4032 non-null   float64
 4    F_2_Z_2 VAV REHEAT Damper Position       4032 non-null   float64
 5    F_2_Z_2: Equipment Power                 4032 non-null   float64
 6    F_2_Z_2: Lights Power                    4032 non-null   float64
 7    F_2_Z_2: Thermostat Temp                 4032 non-null   float64
 8    F_2_Z_2: Thermostat Cooling Setpoint     4032 non-null   float64
 9    F_2_Z_2: Thermostat Heating Setpoint     4032 non-null   float64
dtypes: float64(10)
memory usage: 315.1 K

F_2_Z_2 REHEAT COIL Power   F_2_Z_2 RETURN OUTLET CO2 Concentration  \
0                         0.0                                  891.0525   
1                         0.0                                  891.3950   
2                         0.0                                  889.5625   
3                         0.0                                  888.0449   
4                         0.0                                  886.5617   

    F_2_Z_2 SUPPLY INLET Mass Flow Rate   F_2_Z_2 SUPPLY INLET Temperature  \
0                                0.1056                            12.8023   
1                                0.1056                            12.8391   
2                                0.1056                            12.8048   
3                                0.1056                            12.7999   
4                                0.1056                            12.8000   

    F_2_Z_2 VAV REHEAT Damper Position   F_2_Z_2: Equipment Power  \
0                                  0.2                  1724.1734   
1                                  0.2                   344.8347   
2                                  0.2                   344.8347   
3                                  0.2                   344.8347   
4                                  0.2                   344.8347   

    F_2_Z_2: Lights Power   F_2_Z_2: Thermostat Temp  \
0               2463.1049                    26.2684   
1                  0.0000                    25.5543   
2                  0.0000                    25.0063   
3                  0.0000                    24.6325   
4                  0.0000                    24.3811   

    F_2_Z_2: Thermostat Cooling Setpoint  \
0                                   26.7   
1                                   26.7   
2                                   26.7   
3                                   26.7   
4                                   26.7   

    F_2_Z_2: Thermostat Heating Setpoint  
0                                   15.6  
1                                   15.6  
2                                   15.6  
3                                   15.6  
4                                   15.6

In [202]:
days=[]
for n in range(0,288*14,288):
    days.append(my_df.iloc[n:n+288])
days[12]

F_2_Z_2 REHEAT COIL Power   F_2_Z_2 RETURN OUTLET CO2 Concentration  \
3456                   5046.5664                                  433.9242   
3457                   5056.9087                                  433.9004   
3458                   5068.3906                                  433.8737   
3459                   5078.4455                                  433.8447   
3460                   5088.8542                                  433.8138   
...                          ...                                       ...   
3739                   5039.2064                                  430.4757   
3740                   5053.1125                                  430.5358   
3741                   5062.1923                                  430.5904   
3742                   5070.3521                                  430.6401   
3743                   5078.2081                                  430.6854   

       F_2_Z_2 SUPPLY INLET Mass Flow Rate   F_2_Z_2 SUPPLY INLET Temperature  \
3456                                0.5282                            22.1799   
3457                                0.5282                            22.1991   
3458                                0.5282                            22.2205   
3459                                0.5282                            22.2392   
3460                                0.5282                            22.2585   
...                                    ...                                ...   
3739                                0.5282                            22.1660   
3740                                0.5282                            22.1919   
3741                                0.5282                            22.2088   
3742                                0.5282                            22.2240   
3743                                0.5282                            22.2386   

       F_2_Z_2 VAV REHEAT Damper Position   F_2_Z_2: Equipment Power  \
3456                                  1.0                   344.8347   
3457                                  1.0                   344.8347   
3458                                  1.0                   344.8347   
3459                                  1.0                   344.8347   
3460                                  1.0                   344.8347   
...                                   ...                        ...   
3739                                  1.0                   344.8347   
3740                                  1.0                   344.8347   
3741                                  1.0                   344.8347   
3742                                  1.0                   344.8347   
3743                                  1.0                   344.8347   

       F_2_Z_2: Lights Power   F_2_Z_2: Thermostat Temp  \
3456                     0.0                    24.0017   
3457                     0.0                    24.0017   
3458                     0.0                    24.0017   
3459                     0.0                    24.0017   
3460                     0.0                    24.0017   
...                      ...                        ...   
3739                     0.0                    24.0021   
3740                     0.0                    24.0018   
3741                     0.0                    24.0018   
3742                     0.0                    24.0017   
3743                     0.0                    24.0017   

       F_2_Z_2: Thermostat Cooling Setpoint  \
3456                                   24.0   
3457                                   24.0   
3458                                   24.0   
3459                                   24.0   
3460                                   24.0   
...                                     ...   
3739                                   24.0   
3740                                   24.0   
3741                                   24.0   
3742                                   24.0   
3743  

In [204]:
scaled_data = days

for i, df in enumerate(days):
    scaled_temp = pd.DataFrame(
            preprocessing.MinMaxScaler().fit_transform(df), columns=features)
    scaled_data[i] = scaled_temp

days = scaled_data
days[13]

F_2_Z_2 REHEAT COIL Power   F_2_Z_2 RETURN OUTLET CO2 Concentration  \
0                      0.920380                                  0.000479   
1                      0.921637                                  0.000520   
2                      0.922858                                  0.000558   
3                      0.924054                                  0.000593   
4                      0.925229                                  0.000625   
..                          ...                                       ...   
283                    0.000000                                  0.484599   
284                    0.000000                                  0.488536   
285                    0.000000                                  0.492375   
286                    0.000000                                  0.496109   
287                    0.000000                                  0.499677   

      F_2_Z_2 SUPPLY INLET Mass Flow Rate   F_2_Z_2 SUPPLY INLET Temperature  \
0                                1.000000                           0.789275   
1                                1.000000                           0.790296   
2                                1.000000                           0.791277   
3                                1.000000                           0.792242   
4                                1.000000                           0.793191   
..                                    ...                                ...   
283                              0.262969                           0.047745   
284                              0.263158                           0.047368   
285                              0.263726                           0.047266   
286                              0.264294                           0.047753   
287                              0.199924                           0.048647   

      F_2_Z_2 VAV REHEAT Damper Position   F_2_Z_2: Equipment Power  \
0                                 1.0000                        0.0   
1                                 1.0000                        0.0   
2                                 1.0000                        0.0   
3                                 1.0000                        0.0   
4                                 1.0000                        0.0   
..                                   ...                        ...   
283                               0.2630                        1.0   
284                               0.2632                        1.0   
285                               0.2637                        1.0   
286                               0.2644                        1.0   
287                               0.2000                        0.0   

      F_2_Z_2: Lights Power   F_2_Z_2: Thermostat Temp  \
0                       0.0                   0.159676   
1                       0.0                   0.159676   
2                       0.0                   0.159651   
3                       0.0                   0.159651   
4                       0.0                   0.159651   
..                      ...                        ...   
283                     1.0                   0.829856   
284                     1.0                   0.829856   
285                     1.0                   0.829881   
286                     1.0                   0.829906   
287                     0.0                   0.686702   

      F_2_Z_2: Thermostat Cooling Setpoint  \
0                                      0.0   
1                                      0.0   
2                                      0.0   
3                                      0.0   
4                                      0.0   
..                                     ...   
283                                    1.0   
284                                    1.0   
285                                    1.0   
286                                    1.0   
287                                    1.0   

      F_2_Z_2: Th

In [207]:
def heatmap(df, ax, title):
    corr = df.corr()

    # Omit pairs with weak correlation, try to experiments with this setting
    df_corr = corr[((corr >= .7) | (corr <= -.7))]

    #print("Empty columns:", get_empty_columns_names(df_corr))

    mask = np.triu(np.ones_like(corr))
    sns.heatmap(
        df_corr, 
        cbar=False, 
        mask=mask,
        ax=ax, 
        annot=True, 
        cmap='coolwarm',
        vmin=-1,
        vmax=1,
    )

    ax.title.set_text(title)
    ax.tick_params(
        top=False,
        bottom=False,
        left=False,
        right=False,
    )

In [208]:
fig, ax = plt.subplots( nrows=7,  ncols=2,  sharey=True,  sharex=True,  figsize=(20, 30),  constrained_layout=True)

axes = ax.flatten()

for i, df in enumerate(days):
    heatmap(days[i], axes[i], f"Day {i + 1}")
plt.savefig("heatmaps.png", bbox_inches="tight")
plt.close()

In [209]:
img = Image("heatmaps.png")
img

In [216]:
for i in range(14):
    days[i] = days[i].drop(" F_2_Z_2: Thermostat Heating Setpoint", axis=1)
days[13]

F_2_Z_2 REHEAT COIL Power   F_2_Z_2 RETURN OUTLET CO2 Concentration  \
0                      0.920380                                  0.000479   
1                      0.921637                                  0.000520   
2                      0.922858                                  0.000558   
3                      0.924054                                  0.000593   
4                      0.925229                                  0.000625   
..                          ...                                       ...   
283                    0.000000                                  0.484599   
284                    0.000000                                  0.488536   
285                    0.000000                                  0.492375   
286                    0.000000                                  0.496109   
287                    0.000000                                  0.499677   

      F_2_Z_2 SUPPLY INLET Mass Flow Rate   F_2_Z_2 SUPPLY INLET Temperature  \
0                                1.000000                           0.789275   
1                                1.000000                           0.790296   
2                                1.000000                           0.791277   
3                                1.000000                           0.792242   
4                                1.000000                           0.793191   
..                                    ...                                ...   
283                              0.262969                           0.047745   
284                              0.263158                           0.047368   
285                              0.263726                           0.047266   
286                              0.264294                           0.047753   
287                              0.199924                           0.048647   

      F_2_Z_2 VAV REHEAT Damper Position   F_2_Z_2: Equipment Power  \
0                                 1.0000                        0.0   
1                                 1.0000                        0.0   
2                                 1.0000                        0.0   
3                                 1.0000                        0.0   
4                                 1.0000                        0.0   
..                                   ...                        ...   
283                               0.2630                        1.0   
284                               0.2632                        1.0   
285                               0.2637                        1.0   
286                               0.2644                        1.0   
287                               0.2000                        0.0   

      F_2_Z_2: Lights Power   F_2_Z_2: Thermostat Temp  \
0                       0.0                   0.159676   
1                       0.0                   0.159676   
2                       0.0                   0.159651   
3                       0.0                   0.159651   
4                       0.0                   0.159651   
..                      ...                        ...   
283                     1.0                   0.829856   
284                     1.0                   0.829856   
285                     1.0                   0.829881   
286                     1.0                   0.829906   
287                     0.0                   0.686702   

      F_2_Z_2: Thermostat Cooling Setpoint  
0                                      0.0  
1                                      0.0  
2                                      0.0  
3                                      0.0  
4                                      0.0  
..                                     ...  
283                                    1.0  
284                                    1.0  
285                                    1.0  
286                                    1.0  
287                                    1.0  

[288 rows x 9 columns]

In [217]:
mean_data = []

for i, df in enumerate(days):
    mean_data.append([*df.mean().tolist()])
mean_data

[[0.0,
  0.38750941902202,
  0.5483014903866381,
  0.04393926457194887,
  0.5483059027777778,
  0.5694444444444444,
  0.5694444444444444,
  0.28372159324931007,
  0.33179012345679015],
 [0.0,
  0.3739530530032024,
  0.5643117085279145,
  0.042112774866265724,
  0.5643097222222223,
  0.5833333333333334,
  0.5833333333333334,
  0.20489661997512978,
  0.33179012345679015],
 [0.0,
  0.387319631920791,
  0.5831459832134294,
  0.04046851336924939,
  0.5831468750000001,
  0.5868055555555556,
  0.5868055555555556,
  0.16547424338026873,
  0.33179012345679015],
 [0.0,
  0.38954112919505646,
  0.5881419864108712,
  0.04205344237681338,
  0.5881472222222223,
  0.5659722222222222,
  0.5659722222222222,
  0.20763540250322493,
  0.33179012345679015],
 [0.0,
  0.41643323974406354,
  0.43263986423220974,
  0.044384869972787656,
  0.4326692837124958,
  0.0,
  0.0,
  0.15849133040020186,
  0.5401234567901235],
 [0.0,
  0.7677131558937946,
  0.9236111111111112,
  0.07000660057275382,
  0.9236111111111112

In [224]:
features = [' F_2_Z_2 REHEAT COIL Power',' F_2_Z_2 RETURN OUTLET CO2 Concentration',' F_2_Z_2 SUPPLY INLET Mass Flow Rate',
       ' F_2_Z_2 SUPPLY INLET Temperature',' F_2_Z_2 VAV REHEAT Damper Position',' F_2_Z_2: Equipment Power',
       ' F_2_Z_2: Lights Power', ' F_2_Z_2: Thermostat Temp',
       ' F_2_Z_2: Thermostat Cooling Setpoint']
mean_df = pd.DataFrame(mean_data, columns=features)
mean_df.to_csv('mean_df1.csv', index=False)

reindexed_columns = [' F_2_Z_2 RETURN OUTLET CO2 Concentration',
                     ' F_2_Z_2 REHEAT COIL Power',
                     ' F_2_Z_2 VAV REHEAT Damper Position',
                     ' F_2_Z_2 SUPPLY INLET Mass Flow Rate',
                     ' F_2_Z_2: Equipment Power',
                     ' F_2_Z_2: Lights Power',
                     ' F_2_Z_2: Thermostat Temp',
                     ' F_2_Z_2: Thermostat Cooling Setpoint',
                     ' F_2_Z_2 SUPPLY INLET Temperature'
                    ]
mean_df = mean_df.reindex(columns=reindexed_columns)

mean_df.to_csv('mean_df2.csv', index=False)
mean_df

F_2_Z_2 RETURN OUTLET CO2 Concentration   F_2_Z_2 REHEAT COIL Power  \
0                                   0.387509                    0.000000   
1                                   0.373953                    0.000000   
2                                   0.387320                    0.000000   
3                                   0.389541                    0.000000   
4                                   0.416433                    0.000000   
5                                   0.767713                    0.000000   
6                                   0.365775                    0.014627   
7                                   0.473676                    0.010923   
8                                   0.488278                    0.008720   
9                                   0.329509                    0.000000   
10                                  0.383598                    0.148106   
11                                  0.188437                    0.757542   
12                                  0.249811                    0.700158   
13                                  0.431216                    0.183092   

     F_2_Z_2 VAV REHEAT Damper Position   F_2_Z_2 SUPPLY INLET Mass Flow Rate  \
0                              0.548306                              0.548301   
1                              0.564310                              0.564312   
2                              0.583147                              0.583146   
3                              0.588147                              0.588142   
4                              0.432669                              0.432640   
5                              0.923611                              0.923611   
6                              0.267893                              0.268276   
7                              0.476364                              0.481502   
8                              0.485808                              0.490073   
9                              0.621647                              0.621631   
10                             0.744523                              0.744505   
11                             0.958333                              0.958333   
12                             0.923611                              0.923611   
13                             0.752186                              0.752194   

     F_2_Z_2: Equipment Power   F_2_Z_2: Lights Power  \
0                    0.569444                0.569444   
1                    0.583333                0.583333   
2                    0.586806                0.586806   
3                    0.565972                0.565972   
4                    0.000000                0.000000   
5                    0.000000                0.000000   
6                    0.569444                0.569444   
7                    0.579861                0.579861   
8                    0.572917                0.572917   
9                    0.572917                0.572917   
10                   0.576389                0.576389   
11                   0.000000                0.000000   
12                   0.000000                0.000000   
13                   0.604167                0.604167   

     F_2_Z_2: Thermostat Temp   F_2_Z_2: Thermostat Cooling Setpoint  \
0                    0.283722                               0.331790   
1                    0.204897                               0.331790   
2                    0.165474                               0.331790   
3                    0.207635                               0.331790   
4                    0.158491                               0.540123   
5                    0.438726                               0.000000   
6                    0.491474                               0.657164   
7                    0.613259                               0.627736   
8                    0.621937                               0.625000   
9                    0.444805                               0.834574   


In [225]:
class ChernoffFaces:

    DATA = {
        "HAIR_COLOR": None,
        "SKIN_COLOR": None,    
        "HAIR_LEFT": None, 
        "HAIR_RIGHT": None, 
        "EYEBROW_CURVATURE_LEFT": None,
        "EYEBROW_CURVATURE_RIGHT": None,
        "EYE_HEIGHT_LEFT": None,
        "EYE_HEIGHT_RIGHT": None,
        "PUPIL_SIZE": 0.2,        
        "NOSE_WIDTH": None,
        "MOUTH_HEIGHT": 0.2,
        "MOUTH_WIDTH": None,
    }

    DYNAMIC_PARAMETERS = [
        "HAIR_COLOR",
        "SKIN_COLOR",  
        "HAIR_LEFT",
        "HAIR_RIGHT",
        "EYEBROW_CURVATURE_LEFT",
        "EYEBROW_CURVATURE_RIGHT",
       "EYE_HEIGHT_LEFT",
       "EYE_HEIGHT_RIGHT",
   #    "NOSE_WIDTH",
   #    "MOUTH_WIDTH",
    ]

    def __init__(self, df, labels=None, filename='faces'):

        if not labels:
            self.labels = df.iloc[:,0].values
            df = df[df.columns.drop(df.columns[0])]

        self.data = df

        for index, key in enumerate(self.DYNAMIC_PARAMETERS):
            self.DATA[key] = self.data[self.data.columns[index % len(self.data.columns)]].values.tolist()

        
        self.filename = filename

    def render_face(self, ax, title='', index=None):

        height, width = ax.bbox.height, ax.bbox.width

        self.draw_hair(ax, index, width, height)
        self.draw_face(ax, index, width, height)
        self.draw_l_brow(ax, index)
        self.draw_r_brow(ax, index)
        self.draw_l_eye(ax, index)
        self.draw_r_eye(ax, index)
    #    self.draw_nose(ax, index)   
     #   self.draw_mouth(ax, index)

        ax.title.set_text(title)
        ax.axis('off')
        ax.autoscale()

    def draw_hair(self, ax, index, width, height):

        hair_width = width
        hair_height = height

        colour = plt.cm.coolwarm(self.DATA["HAIR_COLOR"][index])  #настройка цветов

        trapeze = Polygon(
            xy=[
                [0, hair_height * 0.5 * (1 - self.DATA["HAIR_LEFT"][index])],
                [0, hair_height * 0.5],
                [hair_width, hair_height * 0.5],
                [hair_width, hair_height * 0.5 * (1 - self.DATA["HAIR_RIGHT"][index])],
            ], 
            fc=colour
        )
        ax.add_patch(trapeze)

        top = Wedge(
            center=[hair_width / 2, hair_height * 0.5 - 1], 
            r=hair_width / 2,
            theta1=0, 
            theta2=180,
            edgecolor='none', 
            fc=colour,
        )
        ax.add_patch(top)

    def draw_face(self, ax, index, width, height):

        face_width = width * 2/3
        face_height = height * 1/2
        self.UNIT_WIDTH = face_width / 7
        self.UNIT_HEIGHT = face_height / 7
        self.FACE_CENTER = [width / 2, height / 2]

        colour = plt.cm.RdBu(self.DATA["SKIN_COLOR"][index]) #настройка цветов

        ellipse = Ellipse(
        xy=self.FACE_CENTER, 
        width=face_width, 
        height=face_height, 
        edgecolor='black', 
        fc=colour, 
        lw=2
        )
        ax.add_patch(ellipse)

    def draw_l_brow(self, ax, index):

        brow_width = self.UNIT_WIDTH * 1.5
        brow_height =  self.UNIT_HEIGHT * self.DATA["EYEBROW_CURVATURE_LEFT"][index]
        if brow_height == 0:
            brow_height = 0.001

        brow_l_center = [sum(i) for i in zip(*[ 
            self.FACE_CENTER, 
            [brow_width,  self.UNIT_HEIGHT * 1.1] 
        ])]

        brow_l = Arc(
            xy=brow_l_center, 
            width=brow_width, 
            height=brow_height, 
            theta1=0, 
            theta2=180,
            edgecolor='black', 
            fc='None', 
            lw=2
        )
        ax.add_patch(brow_l)

    def draw_r_brow(self, ax, index):

        brow_width = self.UNIT_WIDTH * 1.5
        brow_height =  self.UNIT_HEIGHT * self.DATA["EYEBROW_CURVATURE_RIGHT"][index]

        if brow_height == 0:
            brow_height = 0.001

        brow_r_center = [sum(i) for i in zip(*[ 
            self.FACE_CENTER, 
            [-brow_width,  self.UNIT_HEIGHT * 1.1] 
        ])]

        brow_r = Arc(
            xy=brow_r_center, 
            width=brow_width, 
            height=brow_height, 
            theta1=0, 
            theta2=180,
            edgecolor='black', 
            fc='None', 
            lw=2
        )
        ax.add_patch(brow_r)

    def draw_l_eye(self, ax, index):

        eye_width = self.UNIT_WIDTH * 1.5
        eye_height =  self.UNIT_HEIGHT * self.DATA["EYE_HEIGHT_LEFT"][index] 

        if eye_height == 0:
            eye_height = 0.001

        eye_l_center = [sum(i) for i in zip(*[ 
            self.FACE_CENTER, 
            [-eye_width,  self.UNIT_HEIGHT / 2] 
        ])]

        ellipse = Ellipse(
            xy=eye_l_center, 
            width=eye_width, 
            height=eye_height, 
            edgecolor='black', 
            fc='white', 
            lw=1
        )
        ax.add_patch(ellipse)

        ellipse = Ellipse(
            xy=eye_l_center, 
            width=eye_width / 2, 
            height=eye_height, 
            edgecolor='black', 
            fc='black', 
            lw=1
        )
        ax.add_patch(ellipse)

    def draw_r_eye(self, ax, index):

        eye_width = self.UNIT_WIDTH * 1.5
        eye_height =  self.UNIT_HEIGHT * self.DATA["EYE_HEIGHT_RIGHT"][index] 

        if eye_height == 0:
            eye_height = 0.001

        eye_r_center = [sum(i) for i in zip(*[ 
            self.FACE_CENTER, 
            [eye_width,  self.UNIT_HEIGHT / 2] 
        ])]

        ellipse = Ellipse(
            xy=eye_r_center, 
            width=eye_width, 
            height=eye_height, 
            edgecolor='black', 
            fc='white', 
            lw=1
        )
        ax.add_patch(ellipse)   

        ellipse = Ellipse(
            xy=eye_r_center, 
            width=eye_width / 2, 
            height=eye_height, 
            edgecolor='black', 
            fc='black', 
            lw=1
        )
        ax.add_patch(ellipse)

    def draw_nose(self, ax, index):

        nose_width = self.UNIT_WIDTH * (1 - self.DATA["NOSE_WIDTH"][index])
        nose_height =  self.UNIT_HEIGHT  

        pivot_left = [sum(i) for i in zip(*[ 
            self.FACE_CENTER, 
            [-nose_width / 2,  -nose_height] 
        ])]

        pivot_right = [sum(i) for i in zip(*[ 
            self.FACE_CENTER, 
            [nose_width / 2,  -nose_height] 
        ])]

        pivot_top = self.FACE_CENTER

        points = np.array([pivot_left, pivot_right, pivot_top])
        nose = plt.Polygon(
            points, 
            closed=True, 
            lw=1,
            fc="black", 
            edgecolor='black',
        )
        ax.add_patch(nose)

    def draw_mouth(self, ax, index):

        mouth_width = self.UNIT_WIDTH * 3 * self.DATA["MOUTH_WIDTH"][index] 
        mouth_height = self.UNIT_HEIGHT * 1.5 * self.DATA["MOUTH_HEIGHT"]

        mouth_center = [sum(i) for i in zip(*[ 
            self.FACE_CENTER, 
            [0,  -self.UNIT_HEIGHT * 2] 
        ])]

        ellipse = Ellipse(
            xy=mouth_center, 
            width=mouth_width, 
            height=mouth_height, 
            edgecolor='black', 
            fc="black",  
            lw=1
        )
        ax.add_patch(ellipse)

    def render(self, n_cols=2, n_rows=1, figsize=(2, 2), empty_cols_ids=()):
        fig, ax = plt.subplots(
            nrows=n_rows, 
            ncols=n_cols, 
            figsize=figsize, 
            sharey=True,
            sharex=True,
            constrained_layout=True,
        )
        fig.patch.set_facecolor('white')
        axes = ax.flatten()
        for i, ax in enumerate(axes):
            if i in empty_cols_ids:
                ax.remove()
            if i == 0:
                self.render_face(ax, title=f"Reference", index=i)
                continue
            self.render_face(ax, title=f"Day {i}", index=i)

        plt.savefig(f"{self.filename}.png", bbox_inches="tight")
        plt.close()

In [226]:
reference = pd.DataFrame([(0.5 for _ in range(9))], columns=reindexed_columns)

mean_df = pd.DataFrame(
   preprocessing.MinMaxScaler().fit_transform(mean_df.values), 
    columns=mean_df.columns
)

mean_df = pd.concat([reference, mean_df])
mean_df.index = range(15)

In [227]:
c = ChernoffFaces(mean_df)
c.render(
    n_cols = 5,
    n_rows = 3,
    figsize=(30, 20),
)

In [228]:
img = Image("faces.png")
img